In [1]:
%matplotlib inline
import numpy as np
import pandas as pd
import scipy
import sklearn
import spacy
import matplotlib.pyplot as plt
import seaborn as sns
import re
from nltk.corpus import gutenberg, stopwords
from collections import Counter

In [2]:
# Utility function for standard text cleaning.
def text_cleaner(text):
    # Visual inspection identifies a form of punctuation spaCy does not
    # recognize: the double dash '--'.  Better get rid of it now!
    text = re.sub(r'--',' ',text)
    text = re.sub("[\[].*?[\]]", "", text)
    text = ' '.join(text.split())
    return text
    
# Load and clean the data.
persuasion = gutenberg.raw('austen-persuasion.txt')
alice = gutenberg.raw('carroll-alice.txt')

# The Chapter indicator is idiosyncratic
persuasion = re.sub(r'Chapter \d+', '', persuasion)
alice = re.sub(r'CHAPTER .*', '', alice)
    
alice = text_cleaner(alice)
persuasion = text_cleaner(persuasion)

In [3]:
# Parse the cleaned novels. This can take a bit.
nlp = spacy.load('en')
alice_doc = nlp(alice)
persuasion_doc = nlp(persuasion)

In [4]:
# Group into sentences.
alice_sents = [[sent, "Carroll"] for sent in alice_doc.sents]
persuasion_sents = [[sent, "Austen"] for sent in persuasion_doc.sents]

# Combine the sentences from the two novels into one data frame.
sentences = pd.DataFrame(alice_sents + persuasion_sents)
sentences.head()

0        1
0  (Alice, was, beginning, to, get, very, tired, ...  Carroll
1  (So, she, was, considering, in, her, own, mind...  Carroll
2  (There, was, nothing, so, VERY, remarkable, in...  Carroll
3                                      (Oh, dear, !)  Carroll
4                         (I, shall, be, late, !, ')  Carroll

In [5]:
# Utility function to create a list of the 2000 most common words.
def bag_of_words(text):
    
    # Filter out punctuation and stop words.
    allwords = [token.lemma_
                for token in text
                if not token.is_punct
                and not token.is_stop]
    
    # Return the most common words.
    return [item[0] for item in Counter(allwords).most_common(2000)]
    

# Creates a data frame with features for each word in our common word set.
# Each value is the count of the times the word appears in each sentence.
def bow_features(sentences, common_words):
    
    # Scaffold the data frame and initialize counts to zero.
    df = pd.DataFrame(columns=common_words)
    df['text_sentence'] = sentences[0]
    df['author'] = sentences[1]
    df.loc[:, common_words] = 0
    
    # Process each row, counting the occurrence of words in each sentence.
    for i, sentence in enumerate(df['text_sentence']):
        
        # Convert the sentence to lemmas, then filter out punctuation,
        # stop words, and uncommon words.
        words = [token.lemma_
                 for token in sentence
                 if (
                     not token.is_punct
                     and not token.is_stop
                     and token.lemma_ in common_words
                 )]
        
        # Populate the row with word counts.
        for word in words:
            df.loc[i, word] += 1
        
        # This counter is just to make sure the kernel didn't hang.
        if i % 500 == 0:
            print("Processing row {}".format(i))
            
    return df

# Set up the bags.
alicewords = bag_of_words(alice_doc)
persuasionwords = bag_of_words(persuasion_doc)

# Combine bags to create a set of unique words.
common_words = set(alicewords + persuasionwords)

In [6]:
# Create our data frame with features. This can take a while to run.
word_counts = bow_features(sentences, common_words)
word_counts.head()

Processing row 0
Processing row 500
Processing row 1000
Processing row 1500
Processing row 2000
Processing row 2500
Processing row 3000
Processing row 3500
Processing row 4000
Processing row 4500
Processing row 5000


remembrance bear hollow dig polished topic honesty burst saucepan titter  \
0           0    0      0   0        0     0       0     0        0      0   
1           0    0      0   0        0     0       0     0        0      0   
2           0    0      0   0        0     0       0     0        0      0   
3           0    0      0   0        0     0       0     0        0      0   
4           0    0      0   0        0     0       0     0        0      0   

    ...    cautious rattle delightful affluence lodging foul oftener scream  \
0   ...           0      0          0         0       0    0       0      0   
1   ...           0      0          0         0       0    0       0      0   
2   ...           0      0          0         0       0    0       0      0   
3   ...           0      0          0         0       0    0       0      0   
4   ...           0      0          0         0       0    0       0      0   

                                       text_sentence   author  
0  (Alice, was, beginning, to, get, very, tired, ...  Carroll  
1  (So, she, was, considering, in, her, own, mind...  Carroll  
2  (There, was, nothing, so, VERY, remarkable, in...  Carroll  
3                                      (Oh, dear, !)  Carroll  
4                         (I, shall, be, late, !, ')  Carroll  

[5 rows x 3064 columns]

In [7]:
from sklearn.svm import SVC
from sklearn.model_selection import train_test_split

# Instantiate our model and fit the data.

svm = SVC(kernel = 'linear')
Y = word_counts['author']
X = np.array(word_counts.drop(['text_sentence','author'], 1))

X_train, X_test, y_train, y_test = train_test_split(X, 
                                                    Y,
                                                    test_size=0.4,
                                                    random_state=0)
test = svm.fit(X_test, y_test)
print(X_test.shape, y_test.shape)

print('Training set score:', svm.score(X_train, y_train))
print('\nTest set score:', svm.score(X_test, y_test))

(2128, 3062) (2128,)
Training set score: 0.889655172414

Test set score: 0.978853383459


In [9]:
from sklearn.model_selection import cross_val_score

cross_val_score(test, X_test, y_test, cv=10)

array([ 0.92523364,  0.90186916,  0.90140845,  0.89201878,  0.88732394,
        0.87323944,  0.89622642,  0.89622642,  0.87735849,  0.91509434])

**Running SVC model didn't improve the accuracy over linear regression, which was 93%.  The cross validation scores suggest overfitting, as do the scores comparing testing data to training data.  Providing the model with more data should help combat overfitting.**

In [24]:
# Clean the Leaves data.

leaves = gutenberg.raw('whitman-leaves.txt')
leaves = re.sub(r'VOLUME \w+', '', leaves)
leaves = re.sub(r'CHAPTER \w+', '', leaves)
leaves = text_cleaner(leaves)
print(leaves[:100])

Come, said my soul, Such verses for my Body let us write, (for we are one,) That should I after retu


In [25]:
# Parse cleaned data

leaves_doc = nlp(leaves)

In [26]:
# Group into sentences.

leaves_sents = [[sent, "Whitman"] for sent in leaves_doc.sents]

In [27]:
# Build a new Bag of Words data frame for Emma word counts.
# We'll use the same common words from Alice and Persuasion.
leaves_sentences = pd.DataFrame(leaves_sents)
leaves_bow = bow_features(leaves_sentences, common_words)

print('done')

Processing row 0
Processing row 500
Processing row 1000
Processing row 1500
Processing row 2000
Processing row 2500
Processing row 3000
Processing row 3500
Processing row 4000
Processing row 4500
Processing row 5000
Processing row 5500
done


In [34]:
# Now we can model it!
# Let's use logistic regression again.

# Combine the Leaves sentence data with the Alice data from the test set.

X_Leaves_test = np.concatenate((
    X_train[y_train[y_train=='Carroll'].index],
    leaves_bow.drop(['text_sentence','author'], 1)
), axis=0)
y_Leaves_test = pd.concat([y_train[y_train=='Carroll'],
                         pd.Series(['Whitman'] * leaves_bow.shape[0])])

# Model.

from sklearn.linear_model import LogisticRegression

lr = LogisticRegression()
test = lr.fit(X_Leaves_test, y_Leaves_test)
lr_Leaves_predicted = lr.predict(X_Leaves_test)


print('\nTest set score:', lr.score(X_Leaves_test, y_Leaves_test))
pd.crosstab(y_Leaves_test, lr_Leaves_predicted)


Test set score: 0.954775364475


col_0    Carroll  Whitman
row_0                    
Carroll      719      294
Whitman       10     5699

In [35]:
cross_val_score(test, X_Leaves_test, y_Leaves_test, cv=10)

array([ 0.91679049,  0.93313522,  0.93016345,  0.92261905,  0.91964286,
        0.91220238,  0.91220238,  0.92261905,  0.92261905,  0.92846498])

**Based on the accuracy, the model can accurately distinguish Alice in Wonderland from Leaves of Grass.  The cross validation scores are reasonably close enough to verify accurate model performance.

In [19]:
# Utility function to create a list of the parts of speech.
def parts_of_speech(doc):
    
    for token in doc:
        print(token.text, token.lemma_, token.pos_, token.tag_, token.dep_, token.shape_, token.is_alpha, 
              token.is_stop)


In [20]:
# Creates a data frame with features for each word in our common word set.
# Each value is the count of the times the word appears in each sentence.
def pos_features(sentences, speech):
    
    # Scaffold the data frame and initialize counts to zero.
    df = pd.DataFrame(columns=speech)
    df['text_sentence'] = sentences[0]
    df['author'] = sentences[1]
    df['part of speech'] = sentences[2]
    df.loc[:, speech] = 0
    
    # Process each row, counting the occurrence of words in each sentence.
    for i, sentence in enumerate(df['text_sentence']):
        
        # Convert the sentence to lemmas, then filter out punctuation,
        # stop words, and uncommon words.
        words = [token.lemma_
                 for token in sentence
                 if (
                     not token.is_punct
                     and not token.is_stop
                     and token.lemma_ in speech
                 )]
        
        # Populate the row with word counts.
        for word in words:
            df.loc[i, word] += 1
        
        # This counter is just to make sure the kernel didn't hang.
        if i % 500 == 0:
            print("Processing row {}".format(i))
            
    return df

In [23]:
# Set up the bags.

alicespeech = parts_of_speech(alice_doc)
persuasionspeech = parts_of_speech(persuasion_doc)

# Combine bags to create a set of unique words.

speech = set(alicespeech + persuasionspeech)

Alice alice PROPN NNP nsubj Xxxxx True False
was be VERB VBD aux xxx True True
beginning begin VERB VBG ROOT xxxx True False
to to PART TO aux xx True True
get get VERB VB xcomp xxx True True
very very ADV RB advmod xxxx True True
tired tired ADJ JJ acomp xxxx True False
of of ADP IN prep xx True True
sitting sit VERB VBG pcomp xxxx True False
by by ADP IN prep xx True True
her -PRON- ADJ PRP$ poss xxx True True
sister sister NOUN NN pobj xxxx True False
on on ADP IN prep xx True True
the the DET DT det xxx True True
bank bank NOUN NN pobj xxxx True False
, , PUNCT , punct , False False
and and CCONJ CC cc xxx True True
of of ADP IN conj xx True True
having have VERB VBG pcomp xxxx True False
nothing nothing NOUN NN dobj xxxx True True
to to PART TO aux xx True True
do do VERB VB relcl xx True True
: : PUNCT : punct : False False
once once ADV RB advmod xxxx True True
or or CCONJ CC cc xx True True
twice twice ADV RB conj xxxx True False
she -PRON- PRON PRP nsubj xxx True True
had have

went go VERB VBD ROOT xxxx True False
Alice alice PROPN NNP dobj Xxxxx True False
after after ADP IN prep xxxx True True
it -PRON- PRON PRP pobj xx True True
, , PUNCT , punct , False False
never never ADV RB neg xxxx True True
once once ADV RB advmod xxxx True True
considering consider VERB VBG advcl xxxx True False
how how ADV WRB advmod xxx True True
in in ADP IN prep xx True True
the the DET DT det xxx True True
world world NOUN NN pobj xxxx True False
she -PRON- PRON PRP nsubj xxx True True
was be VERB VBD ccomp xxx True True
to to PART TO aux xx True True
get get VERB VB xcomp xxx True True
out out PART RP prt xxx True True
again again ADV RB advmod xxxx True True
. . PUNCT . punct . False False
The the DET DT det Xxx True False
rabbit rabbit NOUN NN compound xxxx True False
- - PUNCT HYPH punct - False False
hole hole NOUN NN nsubj xxxx True False
went go VERB VBD ROOT xxxx True False
straight straight ADV RB advmod xxxx True False
on on ADV RB prep xx True True
like like ADP IN

herself -PRON- PRON PRP pobj xxxx True True
, , PUNCT , punct , False False
' ' PUNCT '' punct ' False False
after after ADP IN prep xxxx True True
such such ADJ PDT predet xxxx True True
a a DET DT det x True True
fall fall NOUN NN pobj xxxx True False
as as ADP IN prep xx True True
this this DET DT pobj xxxx True True
, , PUNCT , punct , False False
I -PRON- PRON PRP nsubj X True False
shall shall VERB MD aux xxxx True False
think think VERB VB ccomp xxxx True False
nothing nothing NOUN NN dobj xxxx True True
of of ADP IN prep xx True True
tumbling tumble VERB VBG pcomp xxxx True False
down down PART RP prt xxxx True True
stairs stair NOUN NNS dobj xxxx True False
! ! PUNCT . punct ! False False
How how ADV WRB advmod Xxx True False
brave brave ADJ JJ acomp xxxx True False
they -PRON- PRON PRP nsubj xxxx True True
'll will VERB MD aux 'xx False False
all all ADV RB advmod xxx True True
think think VERB VB ROOT xxxx True False
me -PRON- PRON PRP dobj xx True True
at at ADP IN prep xx 

. . PUNCT . punct . False False
' ' PUNCT '' punct ' False False
Dinah'll dinah'll NOUN NNS nsubj Xxxxx'xx False False
miss miss VERB VBP ccomp xxxx True False
me -PRON- PRON PRP dobj xx True True
very very ADV RB advmod xxxx True True
much much ADV RB advmod xxxx True True
to to ADP IN prep xx True True
- - PUNCT HYPH punct - False False
night night NOUN NN pobj xxxx True False
, , PUNCT , punct , False False
I -PRON- PRON PRP nsubj X True False
should should VERB MD aux xxxx True True
think think VERB VB ROOT xxxx True False
! ! PUNCT . punct ! False False
' ' PUNCT '' punct ' False False
( ( PUNCT -LRB- punct ( False False
Dinah dinah PROPN NNP nsubj Xxxxx True False
was be VERB VBD ROOT xxx True True
the the DET DT det xxx True True
cat cat NOUN NN attr xxx True False
. . PUNCT . punct . False False
) ) PUNCT -RRB- punct ) False False
' ' PUNCT '' punct ' False False
I -PRON- PRON PRP nsubj X True False
hope hope VERB VBP ROOT xxxx True False
they -PRON- PRON PRP nsubj xxxx True Tr

she -PRON- PRON PRP nsubj xxx True True
jumped jump VERB VBD conj xxxx True False
up up PART RP prt xx True True
on on ADP IN prep xx True True
to to ADP IN prep xx True True
her -PRON- ADJ PRP$ poss xxx True True
feet foot NOUN NNS pobj xxxx True False
in in ADP IN prep xx True True
a a DET DT det x True True
moment moment NOUN NN pobj xxxx True False
: : PUNCT : punct : False False
she -PRON- PRON PRP nsubj xxx True True
looked look VERB VBD ROOT xxxx True False
up up PART RP prt xx True True
, , PUNCT , punct , False False
but but CCONJ CC cc xxx True True
it -PRON- PRON PRP nsubj xx True True
was be VERB VBD conj xxx True True
all all DET DT dep xxx True True
dark dark ADJ JJ acomp xxxx True False
overhead overhead ADV RB advmod xxxx True False
; ; PUNCT : punct ; False False
before before ADP IN mark xxxx True True
her -PRON- PRON PRP nsubj xxx True True
was be VERB VBD advcl xxx True True
another another DET DT det xxxx True True
long long ADJ JJ amod xxxx True False
passage pass

...

which which ADJ WDT nsubj xxxx True True
sunk sink VERB VBD relcl xxxx True False
with with ADP IN prep xxxx True True
him -PRON- PRON PRP pobj xxx True True
. . PUNCT . punct . False False
The the DET DT det Xxx True False
news news NOUN NN nsubj xxxx True False
of of ADP IN prep xx True True
his -PRON- ADJ PRP$ poss xxx True True
cousins cousin VERB VBZ pobj xxxx True False
Anne anne PROPN NNP poss Xxxx True False
's 's PART POS case 'x False False
engagement engagement NOUN NN nsubj xxxx True False
burst burst NOUN NN ROOT xxxx True False
on on ADP IN prep xx True True
Mr mr PROPN NNP compound Xx True False
Elliot elliot PROPN NNP pobj Xxxxx True False
most most ADV RBS advmod xxxx True True
unexpectedly unexpectedly ADV RB advmod xxxx True False
. . PUNCT . punct . False False
It -PRON- PRON PRP nsubj Xx True False
deranged derange VERB VBD ROOT xxxx True False
his -PRON- ADJ PRP$ poss xxx True True
best good ADJ JJS amod xxxx True False
plan plan NOUN NN dobj xxxx True False
of of

their -PRON- ADJ PRP$ poss xxxx True True
companion companion NOUN NN pobj xxxx True False
, , PUNCT , punct , False False
and and CCONJ CC cc xxx True True
the the DET DT det xxx True True
discovery discovery NOUN NN conj xxxx True False
of of ADP IN prep xx True True
their -PRON- ADJ PRP$ poss xxxx True True
deception deception NOUN NN pobj xxxx True False
in in ADP IN prep xx True True
her -PRON- PRON PRP pobj xxx True True
. . PUNCT . punct . False False
They -PRON- PRON PRP nsubj Xxxx True False
had have VERB VBD ROOT xxx True True
their -PRON- ADJ PRP$ poss xxxx True True
great great ADJ JJ amod xxxx True False
cousins cousin NOUN NNS dobj xxxx True False
, , PUNCT , punct , False False
to to PART TO aux xx True True
be be VERB VB advcl xx True True
sure sure ADJ JJ acomp xxxx True False
, , PUNCT , punct , False False
to to PART TO aux xx True True
resort resort VERB VB xcomp xxxx True False
to to ADP IN prep xx True True
for for ADP IN prep xxx True True
comfort comfort NOUN NN

not not ADV RB neg xxx True True
obliged oblige VERB VBN advcl xxxx True False
to to PART TO aux xx True True
say say VERB VB xcomp xxx True True
that that ADP IN mark xxxx True True
he -PRON- PRON PRP nsubj xx True True
believed believe VERB VBD ccomp xxxx True False
her -PRON- PRON PRP dobj xxx True True
to to PART TO aux xx True True
have have VERB VB aux xxxx True True
been be VERB VBN xcomp xxxx True True
right right ADJ JJ advmod xxxx True False
in in ADP IN prep xx True True
originally originally ADV RB advmod xxxx True False
dividing divide VERB VBG pcomp xxxx True False
them -PRON- PRON PRP dobj xxxx True True
, , PUNCT , punct , False False
he -PRON- PRON PRP nsubj xx True True
was be VERB VBD ROOT xxx True True
ready ready ADJ JJ acomp xxxx True False
to to PART TO aux xx True True
say say VERB VB xcomp xxx True True
almost almost ADV RB advmod xxxx True True
everything everything NOUN NN dobj xxxx True True
else else ADV RB advmod xxxx True True
in in ADP IN prep xx True Tr

glow glow NOUN NN pobj xxxx True False
of of ADP IN prep xx True True
her -PRON- ADJ PRP$ poss xxx True True
spirits spirit NOUN NNS pobj xxxx True False
, , PUNCT , punct , False False
as as ADP IN mark xx True True
her -PRON- ADJ PRP$ poss xxx True True
friend friend NOUN NN nsubj xxxx True False
Anne anne PROPN NNP appos Xxxx True False
's 's PART POS case 'x False False
was be VERB VBD advcl xxx True True
in in ADP IN prep xx True True
the the DET DT det xxx True True
warmth warmth NOUN NN pobj xxxx True False
of of ADP IN prep xx True True
her -PRON- ADJ PRP$ poss xxx True True
heart heart NOUN NN pobj xxxx True False
. . PUNCT . punct . False False
Anne anne PROPN NNP nsubj Xxxx True False
was be VERB VBD ROOT xxx True True
tenderness tenderness NOUN NN acomp xxxx True False
itself -PRON- PRON PRP appos xxxx True True
, , PUNCT , punct , False False
and and CCONJ CC cc xxx True True
she -PRON- PRON PRP nsubj xxx True True
had have VERB VBD conj xxx True True
the the DET DT det xx

TypeError: unsupported operand type(s) for +: 'NoneType' and 'NoneType'

In [ ]:
# Create our data frame with features. This can take a while to run.
speech = pos_features(sentences, speech)
speech.head()